In [1]:
import json
path = 'data/converted_resumes.json'
resumes = json.load(open(path, "r", encoding="utf-8"))
print(len(resumes))

690


In [2]:
res = resumes[0]
print(res)

['Afreen Jamadar\nActive member of IIIT Committee in Third year\n\nSangli, Maharashtra - Email me on Indeed: indeed.com/r/Afreen-Jamadar/8baf379b705e37c6\n\nI wish to use my knowledge, skills and conceptual understanding to create excellent team\nenvironments and work consistently achieving organization objectives believes in taking initiative\nand work to excellence in my work.\n\nWORK EXPERIENCE\n\nActive member of IIIT Committee in Third year\n\nCisco Networking -  Kanpur, Uttar Pradesh\n\norganized by Techkriti IIT Kanpur and Azure Skynet.\nPERSONALLITY TRAITS:\n• Quick learning ability\n• hard working\n\nEDUCATION\n\nPG-DAC\n\nCDAC ACTS\n\n2017\n\nBachelor of Engg in Information Technology\n\nShivaji University Kolhapur -  Kolhapur, Maharashtra\n\n2016\n\nSKILLS\n\nDatabase (Less than 1 year), HTML (Less than 1 year), Linux. (Less than 1 year), MICROSOFT\nACCESS (Less than 1 year), MICROSOFT WINDOWS (Less than 1 year)\n\nADDITIONAL INFORMATION\n\nTECHNICAL SKILLS:\n\n• Programming

In [3]:
restext = res[0] 
labeled_ents = res[1]["entities"]
for ent in labeled_ents:
    print("{} {}".format(ent[2], restext[ent[0]:ent[1]]))

Email Address indeed.com/r/Afreen-Jamadar/8baf379b705e37c6
Links https://www.indeed.com/r/Afreen-Jamadar/8baf379b705e37c6?isid=rex-download&ikw=download-top&co=IN
Skills Database (Less than 1 year), HTML (Less than 1 year), Linux. (Less than 1 year), MICROSOFT
ACCESS (Less than 1 year), MICROSOFT WINDOWS (Less than 1 year)

ADDITIONAL INFORMATION

TECHNICAL SKILLS:

• Programming Languages: C, C++, Java, .net, php.
• Web Designing: HTML, XML
• Operating Systems: Windows […] Windows Server 2003, Linux.
• Database: MS Access, MS SQL Server 2008, Oracle 10g, MySql.
Graduation Year 2016
College Name Shivaji University Kolhapur 
Degree Bachelor of Engg in Information Technology
Graduation Year 2017

College Name CDAC ACTS
Degree PG-DAC
Companies worked at Cisco Networking
Email Address indeed.com/r/Afreen-Jamadar/8baf379b705e37c6
Location Sangli
Name Afreen Jamadar


In [4]:
## for each chosen entity label, count how many documents have a labeled entity for that label, and how many labeled entities total there are for that entity
def gather_candidates(dataset,entity_labels):
    candidates = list()
    for resume in dataset:
        res_ent_labels = list(zip(*resume[1]["entities"]))[2]
        if set(entity_labels).issubset(res_ent_labels):
            candidates.append(resume)
    return candidates

chosen_entity_labels = ["Name", "Skills", "Designation", "Companies worked at", "College Name"]
training_data = gather_candidates(resumes, chosen_entity_labels)
print("Gathered {} training examples".format(len(training_data)))

Gathered 370 training examples


In [5]:
## filter all annotation based on filter list
def filter_ents(ents, filter):
    filtered = [ent for ent in ents if ent[2] in filter]
    return filtered

## TODO use method above to remove all but relevant (chosen) entity annotations and store in X variable
X = resumes
for res in X:
    res[1]["entities"] = filter_ents(res[1]["entities"], chosen_entity_labels)

print(X[0])

['Afreen Jamadar\nActive member of IIIT Committee in Third year\n\nSangli, Maharashtra - Email me on Indeed: indeed.com/r/Afreen-Jamadar/8baf379b705e37c6\n\nI wish to use my knowledge, skills and conceptual understanding to create excellent team\nenvironments and work consistently achieving organization objectives believes in taking initiative\nand work to excellence in my work.\n\nWORK EXPERIENCE\n\nActive member of IIIT Committee in Third year\n\nCisco Networking -  Kanpur, Uttar Pradesh\n\norganized by Techkriti IIT Kanpur and Azure Skynet.\nPERSONALLITY TRAITS:\n• Quick learning ability\n• hard working\n\nEDUCATION\n\nPG-DAC\n\nCDAC ACTS\n\n2017\n\nBachelor of Engg in Information Technology\n\nShivaji University Kolhapur -  Kolhapur, Maharashtra\n\n2016\n\nSKILLS\n\nDatabase (Less than 1 year), HTML (Less than 1 year), Linux. (Less than 1 year), MICROSOFT\nACCESS (Less than 1 year), MICROSOFT WINDOWS (Less than 1 year)\n\nADDITIONAL INFORMATION\n\nTECHNICAL SKILLS:\n\n• Programming

In [8]:
import random
from pathlib import Path
import spacy 
from spacy.util import minibatch, compounding


def train_spacy_ner(training_data ,model, n_iter, debug=False):
    if model is not None:
        nlp = spacy.load(model)  # load existing spaCy model
        print("Loaded model '%s'" % model)
    else:
        nlp = spacy.blank("en")  # create blank Language class
        print("Created blank 'en' model")

    # create the built-in pipeline components and add them to the pipeline
    # nlp.create_pipe works for built-ins that are registered with spaCy
    if "ner" not in nlp.pipe_names:
        ner = nlp.create_pipe("ner")
        nlp.add_pipe(ner, last=True)
    # otherwise, get it so we can add labels
    else:
        ner = nlp.get_pipe("ner")

    # add labels
    for _, annotations in training_data:
        for ent in annotations.get("entities"):
            ner.add_label(ent[2])

    # get names of other pipes to disable them during training
    other_pipes = [pipe for pipe in nlp.pipe_names if pipe != "ner"]
    with nlp.disable_pipes(*other_pipes):  # only train NER
        # reset and initialize the weights randomly – but only if we're
        # training a new model
        if model is None:
            nlp.begin_training()

        ## gather up docs that throw exception (only in debug mode)
        baddocs = set()

        for itn in range(n_iter):
            random.shuffle(training_data)
            losses = {}
            # batch up the examples using spaCy's minibatch
            # singlebatch for debug
            singlebatch = 1
            compoundbatch = compounding(4.0, 32.0, 1.001)
            batchsize = singlebatch if debug else compoundbatch
            batches = minibatch(training_data, size=batchsize)
            for batch in batches:
                texts, annotations = zip(*batch)
                try:
                    nlp.update(
                        texts,  # batch of texts
                        annotations,  # batch of annotations
                        drop=0.5,  # dropout - make it harder to memorise data
                        losses=losses,
                    )
                except Exception:
                    if debug:
                        print("Exception thrown when processing doc:")
                        print(texts,annotations)
                        baddocs.add(batch[0][0])
                        continue
            print("Losses", losses)
    return nlp,baddocs


def load_spacy_model(model_dir):
    print("Loading from", model_dir)
    nlp = spacy.load(model_dir)
    return nlp

def save_spacy_model(model, output_dir):
    output_dir = Path(output_dir)
    if not output_dir.exists():
        output_dir.mkdir()
    model.to_disk(output_dir)
    print("Saved model to", output_dir)

In [10]:
def remove_bad_data(training_data):
    print()
    model, baddocs = train_spacy_ner(training_data, model = None, debug=True, n_iter=1)
    ## training data is list of lists with each list containing a text and annotations
    ## baddocs is a set of strings/resume texts.
    ## TODO complete implementation to filter bad docs and store filter result (good docs) in filtered variable
    filtered = [data for data in training_data if data[0] not in baddocs]
    print("Unfiltered training data size: ",len(training_data))
    print("Filtered training data size: ", len(filtered))
    print("Bad data size: ", len(baddocs))
    return filtered

X = remove_bad_data(X)
print("Done")


Created blank 'en' model
Exception thrown when processing doc:
('Amrata Rajani\nTo Assistant Sales Manager - Urbanpro\n\nMumbai, Maharashtra - Email me on Indeed: indeed.com/r/Amrata-Rajani/e61cefb41204829f\n\nTo achieve highest standards in the profession through hard work, Sincerity and determination\nand to\nprovide my best services at all times to my organizations.\n\nWORK EXPERIENCE\n\nTo Assistant Sales Manager\n\nUrbanpro -\n\nDecember 2014 to Present\n\n• Contacting potential or existing customers to inform them about a product\n• Answering questions about products or the company\n• Asking questions to understand customer requirements and close sales\n• Direct prospects to the field sales team when needed\n• Handle grievances to preserve the company\'s reputation\n• Go the "extra mile" to meet sales quota and facilitate future sales\n• Proven track record of successfully meeting sales quota preferably over the phone\n• Promoted To TEAM LEADER -Sales:\n\n• Run New Client on boa

Exception thrown when processing doc:
("Abbas Reshamwala\nAssistant Sales Manager - Sterling Holiday Resorts Ltd\n\nMumbai, Maharashtra - Email me on Indeed: indeed.com/r/Abbas-Reshamwala/\na4dbb5e6ed9b5682\n\nA Challenging position in an organization, where my professional\nexperiences and skills are utilized to the fullest in enhancing personal as\nwell as organizational growth.\n\nWORK EXPERIENCE\n\nAssistant Sales Manager\n\nSterling Holiday Resorts Ltd -  Mumbai, Maharashtra -\n\nMay 2016 to Present\n\nJob Profile,\n• To promote lifestyle and luxury memberships to HNI's\nclientele in Mumbai and Outstation Venues.\n• Forecasting and planning the daily and weekly sales activities.\n• Monitor market intelligence with competitors.\n• To solve members queries.\n• Expedite daily reports.\n• Leading the Team.\n• Taking one-on-one session with Executive for improvement.\n• Short-listing resumes as per job profile.\n• Sales Productivity and preparing daily MIS.\n• Identify Training Needs.\

Exception thrown when processing doc:
('RIYAZ SHAIKH\nMumbai, Maharashtra - Email me on Indeed: indeed.com/r/RIYAZ-SHAIKH/d747d14cb4190d9d\n\nWilling to relocate: Anywhere\n\nWORK EXPERIENCE\n\nSTATION MASTER\n\nQatar rail -\n\nMay 2018 to Present\n\nStation Manager\n\nMumbai Monorail -\n\nMay 2015 to May 2018\n\nBase manager\n\nAVA Merchandising Solutions Pvt. Ltd -\n\nFebruary 2013 to May 2015\n\nManager Operations and sales\n\nKGN Enterprises -\n\nMarch 2009 to December 2012\n\nDuty Manager\n\nEssar Telecom -\n\nMay 2008 to February 2009\n\nSales Associate\n\nEssar Telecom -\n\nJuly 2007 to May 2008\n\nEDUCATION\n\nMcom\n\nMUMBAI UNIVERSITY\n\nBcom in Account and management\n\nMumbai university -  Mumbai, Maharashtra\n\nhttps://www.indeed.com/r/RIYAZ-SHAIKH/d747d14cb4190d9d?isid=rex-download&ikw=download-top&co=IN\n\n\nSKILLS\n\nSales Manager (5 years), Operations (3 years), Documentation (2 years), Handling sales team\n(5 years), Sales Management (5 years)',) ({'entities': [[849, 8

Exception thrown when processing doc:
("Phiroz Hoble\nAccount Manager - Sales\n\nMumbai, Maharashtra - Email me on Indeed: indeed.com/r/Phiroz-Hoble/cc65ba00a1aaa5b9\n\nA sales hungry professional and very commercial in management approach, thrives on driving\ntargets, and enjoys leading teams and achieving results through people management. Always\nensures best practice and consistency across all business operations and coupled with the\nrequired level of enthusiasm and resilience to be able to sell into all market sectors. Ability to learn\nabout new products & markets quickly, well spoken & an excellent communicator.\n\nPROFESSIONAL SNAPSHOT:\n\n• A result oriented aspirant with 13 years of experience in core Sales, Sales Research, Account\nManagement and BPO sector\n• Excellent track record at Jaincotech, successfully moved to the next level in debt recovery at\nSpanco Respondez and as a Branch Manager at Ample Sales & Marketing\n\nWilling to relocate: Anywhere\n\nWORK EXPERIENCE\n

Exception thrown when processing doc:
("Girish Acharya\nTechnical Architect & Sr. Software Engineer\n\nPune, Maharashtra - Email me on Indeed: indeed.com/r/Girish-Acharya/6757f94ee9f4ec23\n\nI would like to describe myself as a hard-core software engineer and technical architect\npassionate for technology and someone who loves to take challenges head-on. I have been using\ncombined engineering principles wherein I was responsible for designing, developing, testing,\ndeploying and monitoring highly scalable distributed applications and services. \n\nWhile I have always been working using Microsoft technologies, I got chance to work for Microsoft\nin as a full-time employee last year. My focus as part of this role was as a Dev Ops/Site Reliability\nEngineer. The main requirement of this role was to keep-lights-on in all data centers for Windows\nDeveloper Center. While Service Engineering aspect was the main requirement, I used my\ntechnical architect and software tools for inside-out an

...

Exception thrown when processing doc:
('Roshan Sinha\nApplication Developer - SAP ABAP\n\nKolkata, West Bengal - Email me on Indeed: indeed.com/r/Roshan-Sinha/ab398efcd288724f\n\nWilling to relocate to: Kolkata, West Bengal - Bangalore City, Karnataka - NCR, Delhi\n\nWORK EXPERIENCE\n\nApplication Developer\n\nSAP ABAP -  Kolkata, West Bengal -\n\nMarch 2011 to April 2018\n\nJoined as Associate System Engineer, worked as Application Developer for maintenance and\ndevelopment of SAP systems for clients from Distribution, Chemicals and Petrochemicals and\nIndustrial sectors.\n\nApplication Developer\n\nIBM India Pvt. Ltd. -\n\nApril 2011 to March 2018\n\nApplication Development and Maintainence services on SAP using ABAP as programming\nlanguage.\n\nApplication Developer\n\nSAP ABAP -  Kolkata, West Bengal -\n\nJune 2017 to November 2017\n\nNon-ALE Outbound File Interfaces for Forward and Reverse Logistics Application from SAP to EMM\nsystem Return, Replacement and Dispatched IMEI and SI

Exception thrown when processing doc:
('Sanjivv Dawalle\nSales Manager - Quikr India Pvt Ltd\n\nMumbai, Maharashtra - Email me on Indeed: indeed.com/r/Sanjivv-Dawalle/\nbe6e06e14054819c\n\n➢ A creative and innovative professional with decade of extensive experience in marketing, brand\nbuilding, revenue expansion, account relationship management with P & L responsibility.\n➢ A keen strategist with expertise in managing entire operations with key focus on profitability\nby ensuring optimal utilization of resources. Attained proficiency in Business Development and\nManaging Business Operations.\n\nWilling to relocate to: Mumbai, Maharashtra - Navi Mumbai, Maharashtra - Thane, Maharashtra\n\nWORK EXPERIENCE\n\nSales Manager\n\nQuikr India Pvt Ltd -\n\nDecember 2015 to Present\n\nWork profile and Responsibilities\n\n➢ Generate sales form B2B as well as B2C market and help them to generate the business leads\ninto their respective category by registering them on Quikr.com portal.\n➢ Looking

Exception thrown when processing doc:
('Vijayalakshmi Govindarajan\nSAP as a Consultant - SAP Basis\n\nChennai, Tamil Nadu - Email me on Indeed: indeed.com/r/Vijayalakshmi-Govindarajan/\nd71bfb70a66b0046\n\nWilling to relocate: Anywhere\n\nWORK EXPERIENCE\n\nSAP as a Consultant\n\nSAP Basis -\n\nMay 2012 to Present\n\nInvolved in 3 support Projects and 1 implementation Project.\n• System Build, System Refresh, system upgrade and system maintenance activities.\n• Self-motivated and goal-oriented, with a strong ability to organize and prioritize tasks\nefficiently.\n• Excellent team player with good communication, analytical, problem solving skills.\n• Certification Done: Oracle certified Java Programmer\n• Finished Diploma in Java course from NIIT\n\nEDUCATION\n\nMCA in Computer Applications\n\nThiagarajar School of Management -  Madurai, Tamil Nadu\n\nBSc\n\nSri Sathya Sai Institute of Higher Learning -  Anantapur, Andhra Pradesh\n\nHSC\n\nTVS Lakshmi Matriculation Higher Secondary Sch

Exception thrown when processing doc:
('Sharadhi TP\nTumkur, Karnataka - Email me on Indeed: indeed.com/r/Sharadhi-TP/5c19a374f49b560e\n\nLooking to pursue a career in DevOps and seeking work where I can learn, contribute and grow\nas an individual.\n\nWilling to relocate: Anywhere\n\nWORK EXPERIENCE\n\nfreshers\n\nVersion control: GIT\n• Creation of repository\n• Commit the code to the repository and also push operations on it.\n• Creation of branches and performing the operations on it.\n\nContinuous integration: Jenkins\n• Creation of jobs\n• Creation of Freestyle and Maven projects\n• Build the tests according to the projects.\n• Creation of pipeline projects.\n• Configuration of Jenkins and using GIT with Jenkins.\n\nConfiguration Management: Ansible\n• Architecture of ansible and its working.\n\nContainer tool: Docker\n• Docker Architecture.\n• Docker login and use of Docker hub.\n• Image operations.\n• Use of Containers in the Dockers.\n• Push and pull from the Docker hub\n\nMon

Losses {'ner': 42952.58551975506}
Unfiltered training data size:  690
Filtered training data size:  483
Bad data size:  156
Done


In [11]:
train_size = int(len(X)*0.8)
train = X[:train_size]
test = X[train_size:]

In [45]:
custom_ner,_= train_spacy_ner(train, model=None, n_iter=200)
print("Done")

Created blank 'en' model
Losses {'ner': 36202.762252289875}
Losses {'ner': 23521.414487454225}
Losses {'ner': 27404.817256584764}
Losses {'ner': 23242.685861343503}
Losses {'ner': 30496.47046822071}
Losses {'ner': 20656.449075523935}
Losses {'ner': 21771.317111202457}
Losses {'ner': 20172.50629659387}
Losses {'ner': 20541.337995852533}
Losses {'ner': 19742.01059761468}
Losses {'ner': 22315.795547152855}
Losses {'ner': 16252.774338713974}
Losses {'ner': 15616.21761898178}
Losses {'ner': 20317.54175303669}
Losses {'ner': 19262.502457359325}
Losses {'ner': 14944.338241359568}
Losses {'ner': 15862.975010979717}
Losses {'ner': 14962.75772042925}
Losses {'ner': 16377.564313872057}
Losses {'ner': 14250.533254776983}
Losses {'ner': 14616.454539319428}
Losses {'ner': 13208.582989491206}
Losses {'ner': 13740.928675663516}
Losses {'ner': 14358.940935654387}
Losses {'ner': 13395.088301418085}
Losses {'ner': 12998.74083917784}
Losses {'ner': 12197.182864064634}
Losses {'ner': 11204.746158207103}
Lo

In [46]:
resume = test[2]
doc = custom_ner(resume[0])
from spacy import displacy 
displacy.render(doc, style="ent",jupyter=True)

In [47]:
print("PREDICTED:")
for ent in doc.ents:
    print(ent.label_, ent.text)
print("LABELED:")
for ent in (resume[1]["entities"]):
    print(resume[0][ent[0]:ent[1]])    

PREDICTED:
Name Manojkumar Bora
Designation Sales Manager
Designation Sales Manager
Companies worked at Anup Enterprises
Designation Sales Manager
Skills CONFIDENT
Skills PROACTIVE
Skills PROBLEM SOLVER
Skills SELF MOTIVATED
Skills SELF-STARTER
LABELED:
1. Strong problem solver with commitment to excellence
2. Highly presentable, confident and strong communicators
3. Must be highly motivated and mature in their business dealings
4. Demonstrate capability to get final result.
5. A proactive self-starter who can operate both individually and as a part of
SELF-STARTER
SELF MOTIVATED
 PROBLEM SOLVER
PROACTIVE
CONFIDENT
Kewalaram Ghanshyamdas
Sales Person
Popley Gold Plazza
Sales Manager
Anup Enterprises
Sales Manager
Sales Manager
Manojkumar Bora


In [61]:
save_spacy_model(custom_ner, '/Users/shishen/Insight_Data_Science/Resume_Standardization/custom_ner/')

Saved model to /Users/shishen/Insight_Data_Science/Resume_Standardization/custom_ner


In [49]:
for text,_ in train:
    doc = custom_ner(text)
    print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
    print("Tokens", [(t.text, t.ent_type_, t.ent_iob) for t in doc])

Entities [('Ashok Kunam', 'Name'), ('Team Lead', 'Designation'), ('Microsoft', 'Companies worked at'), ('Microsoft', 'Companies worked at'), ('Team Lead', 'Designation'), ('Microsoft', 'Companies worked at'), ('Jawaharlal Nehru Technology University', 'College Name'), ('database (Less than 1 year), Git (Less than 1 year), Java (Less than 1 year), JIRA (Less than 1\nyear), life cycle (Less than 1 year)', 'Skills')]
Tokens [('Ashok', 'Name', 3), ('Kunam', 'Name', 1), ('\n', '', 2), ('Team', 'Designation', 3), ('Lead', 'Designation', 1), ('-', '', 2), ('Microsoft', 'Companies worked at', 3), ('\n\n', '', 2), ('-', '', 2), ('Email', '', 2), ('me', '', 2), ('on', '', 2), ('Indeed', '', 2), (':', '', 2), ('indeed.com/r/Ashok-Kunam/7aac8767aacf10a0', '', 2), ('\n\n', '', 2), ('•', '', 2), ('Software', '', 2), ('Engineering', '', 2), ('professional', '', 2), ('with', '', 2), ('over', '', 2), ('2.5', '', 2), ('years', '', 2), ('of', '', 2), ('experience', '', 2), ('in', '', 2), ('development', 

Entities [('Prashant Jagtap', 'Name'), ('Account Delivery Manager', 'Designation'), ('Hewlett Packard India Sales Pvt Ltd', 'Companies worked at'), ('Account Delivery Manager', 'Designation'), ('Hewlett Packard India Sales Pvt Ltd', 'Companies worked at'), ('Project Manager', 'Designation'), ('Royal Bank of Scotland', 'Companies worked at'), ('CMS Infosystems Pvt. Ltd', 'Companies worked at'), ('Channel Manager', 'Designation'), ('OMNITECH Info solutions Limited', 'Companies worked at'), ('Channel Consultant', 'Designation'), ('HCL Infosystems Limited', 'Companies worked at'), ('Customer Support Engineer', 'Designation'), ('APLAB Ltd', 'Companies worked at'), ('Information Technology- University of Mumbai.', 'College Name'), ('Mumbai University', 'College Name'), ('CLIENTS', 'Skills'), ('SATISFACTION', 'Skills'), ('SOLUTIONS', 'Skills'), ('TRAINING', 'Skills'), ('COLLECTION', 'Skills')]
Tokens [('Prashant', 'Name', 3), ('Jagtap', 'Name', 1), ('\n', '', 2), ('"', '', 2), ('Account', 'De

Entities [('Madhuri Sripathi', 'Name'), ('Senior project engineer', 'Designation'), ('Wipro', 'Companies worked at'), ('Senior project engineer', 'Designation'), ('Cisco', 'Companies worked at'), ('Cisco', 'Companies worked at'), ('Wipro', 'Companies worked at'), ('Senior project engineer', 'Designation'), ('Senior software engineer', 'Designation'), ('Wipro', 'Companies worked at'), ('Cisco', 'Companies worked at'), ('Cisco', 'Companies worked at'), ('PES college', 'College Name'), ('LINUX', 'Skills'), ('UNIX', 'Skills'), ('ipsec', 'Skills'), ('tcl', 'Skills')]
Tokens [('Madhuri', 'Name', 3), ('Sripathi', 'Name', 1), ('\n', '', 2), ('Banglore', '', 2), (',', '', 2), ('Karnataka', '', 2), (',', '', 2), ('Karnataka', '', 2), ('-', '', 2), ('Email', '', 2), ('me', '', 2), ('on', '', 2), ('Indeed', '', 2), (':', '', 2), ('indeed.com/r/Madhuri-', '', 2), ('\n', '', 2), ('Sripathi/04a52a262175111c', '', 2), ('\n\n', '', 2), ('Around', '', 2), ('4', '', 2), ('years', '', 2), ('of', '', 2), (

Entities [('Sameer More', 'Name'), ('Assistant Manager Sales', 'Designation'), ('Kotak Mahindra Bank', 'Companies worked at'), ('Mumbai university', 'College Name'), ('Mumbai University', 'College Name')]
Tokens [('Sameer', 'Name', 3), ('More', 'Name', 1), ('\n', '', 2), ('Mumbai', '', 2), (',', '', 2), ('Maharashtra', '', 2), ('-', '', 2), ('Email', '', 2), ('me', '', 2), ('on', '', 2), ('Indeed', '', 2), (':', '', 2), ('indeed.com/r/Sameer-More/183ccba2cb00a02a', '', 2), ('\n\n', '', 2), ('Looking', '', 2), ('for', '', 2), ('opportunity', '', 2), ('to', '', 2), ('explore', '', 2), ('my', '', 2), ('skills', '', 2), ('and', '', 2), ('become', '', 2), ('a', '', 2), ('Professional', '', 2), ('in', '', 2), ('Industry', '', 2), ('.', '', 2), ('An', '', 2), ('opportunity', '', 2), ('\n', '', 2), ('that', '', 2), ('gives', '', 2), ('platform', '', 2), (',', '', 2), ('good', '', 2), ('working', '', 2), ('environment', '', 2), ('to', '', 2), ('put', '', 2), ('100', '', 2), ('%', '', 2), ('effo

Entities [('Sanand Pal', 'Name'), ('SQL and MSBI Developer', 'Designation'), ('Assistant Consultant', 'Designation'), ('TCS', 'Companies worked at'), ('MICROSOFT', 'Companies worked at'), ('East Point College of Engg. & Tech.', 'College Name'), ('Sql Server, Ssis, T-SQL, ETL, SSRS', 'Skills')]
Tokens [('Sanand', 'Name', 3), ('Pal', 'Name', 1), ('\n', '', 2), ('SQL', 'Designation', 3), ('and', 'Designation', 1), ('MSBI', 'Designation', 1), ('Developer', 'Designation', 1), ('with', '', 2), ('experience', '', 2), ('in', '', 2), ('Azure', '', 2), ('SQL', '', 2), ('and', '', 2), ('Data', '', 2), ('Lake', '', 2), ('\n', '', 2), ('store', '', 2), ('.', '', 2), ('\n\n', '', 2), ('Hyderabad', '', 2), (',', '', 2), ('Telangana', '', 2), ('-', '', 2), ('Email', '', 2), ('me', '', 2), ('on', '', 2), ('Indeed', '', 2), (':', '', 2), ('indeed.com/r/Sanand-Pal/5c99c42c3400737c', '', 2), ('\n\n', '', 2), ('I', '', 2), ('intend', '', 2), ('to', '', 2), ('establish', '', 2), ('myself', '', 2), ('as', ''

...

Entities [('Satyendra Singh', 'Name'), ('Sales Manager', 'Designation'), ('Sales Manager', 'Designation'), ('Edelweiss investment adviser LIMITEDc', 'Companies worked at'), ('SALES MANAGER', 'Designation'), ('SOLDES TECHNO PRIVATE LIMITED', 'Companies worked at'), ('Senior Sales officer', 'Designation'), ('HDB FINANCIAL SERVICES LTD', 'Companies worked at'), ('Senior Export Executive', 'Designation'), ('TECHNOMAG INDUSTRIES MUMBAI', 'Companies worked at'), ('Administrative Executive', 'Designation'), ('AM CONSULTANTS MUMBAI', 'Companies worked at'), ('Guru Nanak College Mumbai', 'College Name'), ('EXCEL', 'Skills'), ('INTERNET EXPLORER', 'Skills'), ('MS WORD', 'Skills'), ('OUTLOOK', 'Skills'), ('POWERPOINT', 'Skills')]
Tokens [('Satyendra', 'Name', 3), ('Singh', 'Name', 1), ('\n', '', 2), ('Sales', 'Designation', 3), ('Manager', 'Designation', 1), ('\n\n', '', 2), ('Mumbai', '', 2), (',', '', 2), ('Maharashtra', '', 2), ('-', '', 2), ('Email', '', 2), ('me', '', 2), ('on', '', 2), ('In

Entities [('Georgia Institute of Technology', 'College Name'), ('Georgia Institute of Technology', 'College Name'), ('Amrita School of Engineering', 'College Name'), ('C++', 'Skills'), ('LINUX', 'Skills'), ('JAVA', 'Skills'), ('Oracle', 'Skills')]
Tokens [('Ajay', '', 2), ('Elango', '', 2), ('\n', '', 2), ('Software', '', 2), ('Engineer', '', 2), ('\n\n', '', 2), ('Bangalore', '', 2), ('City', '', 2), (',', '', 2), ('Karnataka', '', 2), (',', '', 2), ('Karnataka', '', 2), ('-', '', 2), ('Email', '', 2), ('me', '', 2), ('on', '', 2), ('Indeed', '', 2), (':', '', 2), ('indeed.com/r/Ajay-', '', 2), ('\n', '', 2), ('Elango/3c79ad143578c3f2', '', 2), ('\n\n', '', 2), ('•', '', 2), ('7', '', 2), ('+', '', 2), ('years', '', 2), ('of', '', 2), ('professional', '', 2), ('work', '', 2), ('experience', '', 2), ('as', '', 2), ('a', '', 2), ('Software', '', 2), ('Engineer', '', 2), ('with', '', 2), ('core', '', 2), ('expertise', '', 2), ('in', '', 2), ('C++', '', 2), ('\n', '', 2), ('programming', 

Entities [('Shodhan Pawar', 'Name'), ('Mithibai College', 'College Name'), ('Territory Sales Manager', 'Designation'), ('Bhagyashree Textiles', 'Companies worked at'), ('Anudhan Creations', 'Companies worked at'), ('Mithibai College', 'College Name'), ('Microsoft Office', 'Skills'), ('Photoshop', 'Skills'), ('Corel Draw', 'Skills'), ('Illustrator', 'Skills')]
Tokens [('Shodhan', 'Name', 3), ('Pawar', 'Name', 1), ('\n', '', 2), ('Mumbai', '', 2), (',', '', 2), ('Maharashtra', '', 2), ('-', '', 2), ('Email', '', 2), ('me', '', 2), ('on', '', 2), ('Indeed', '', 2), (':', '', 2), ('indeed.com/r/Shodhan-', '', 2), ('\n', '', 2), ('Pawar/3caac8422d269523', '', 2), ('\n\n', '', 2), ('*', '', 2), ('B.Sc', '', 2), ('.', '', 2), ('in', '', 2), ('Physics', '', 2), ('from', '', 2), ('Mithibai', 'College Name', 3), ('College', 'College Name', 1), ('(', '', 2), ('Mumbai', '', 2), ('University', '', 2), (')', '', 2), ('\n', '', 2), ('*', '', 2), ('9', '', 2), ('Years', '', 2), ('of', '', 2), ('Experi

Entities [('Shaik Tazuddin', 'Name')]
Tokens [('Shaik', 'Name', 3), ('Tazuddin', 'Name', 1), ('\n', '', 2), ('Senior', '', 2), ('Process', '', 2), ('Executive', '', 2), ('-', '', 2), ('STAR', '', 2), ('India', '', 2), ('\n\n', '', 2), ('Bengaluru', '', 2), (',', '', 2), ('Karnataka', '', 2), ('-', '', 2), ('Email', '', 2), ('me', '', 2), ('on', '', 2), ('Indeed', '', 2), (':', '', 2), ('indeed.com/r/Shaik-Tazuddin/1366179051f145eb', '', 2), ('\n\n', '', 2), ('To', '', 2), ('establish', '', 2), ('myself', '', 2), ('as', '', 2), ('a', '', 2), ('sincere', '', 2), ('and', '', 2), ('honest', '', 2), ('employee', '', 2), ('in', '', 2), ('a', '', 2), ('challenging', '', 2), ('organization', '', 2), ('by', '', 2), ('using', '', 2), ('my', '', 2), ('\n', '', 2), ('attitude', '', 2), ('and', '', 2), ('learning', '', 2), (',', '', 2), ('thus', '', 2), ('enhancing', '', 2), ('my', '', 2), ('skills', '', 2), ('along', '', 2), ('with', '', 2), ('the', '', 2), ('growth', '', 2), ('of', '', 2), ('the'

Entities [('Vishwanath P', 'Name'), ('Senior Executive (MIS & Audit)', 'Designation'), ('LabourNet Services India\nPvt Ltd', 'Companies worked at')]
Tokens [('Vishwanath', 'Name', 3), ('P', 'Name', 1), ('\n', '', 2), ('Senior', 'Designation', 3), ('Executive', 'Designation', 1), ('(', 'Designation', 1), ('MIS', 'Designation', 1), ('&', 'Designation', 1), ('Audit', 'Designation', 1), (')', 'Designation', 1), ('-', '', 2), ('Job', '', 2), ('Profile', '', 2), ('in', '', 2), ('LabourNet', 'Companies worked at', 3), ('Services', 'Companies worked at', 1), ('India', 'Companies worked at', 1), ('\n', 'Companies worked at', 1), ('Pvt', 'Companies worked at', 1), ('Ltd', 'Companies worked at', 1), ('\n\n', '', 2), ('Bengaluru', '', 2), (',', '', 2), ('Karnataka', '', 2), ('-', '', 2), ('Email', '', 2), ('me', '', 2), ('on', '', 2), ('Indeed', '', 2), (':', '', 2), ('indeed.com/r/Vishwanath-P/06a16ac2d087d3c9', '', 2), ('\n\n', '', 2), ('I', '', 2), ('look', '', 2), ('forward', '', 2), ('to', ''

In [50]:
from spacy.gold import biluo_tags_from_offsets
import pandas as pd
from IPython.display import display, HTML

## returns a pandas dataframe with tokens, prediction, and true (Gold Standard) annotations of tokens
def make_bilou_df(nlp,resume):
    """
    param nlp - a trained spacy model
    param resume - a resume from our train or test set
    """
    doc = nlp(resume[0])
    bilou_ents_predicted = biluo_tags_from_offsets(doc, [(ent.start_char,ent.end_char,ent.label_)for ent in doc.ents])
    bilou_ents_true = biluo_tags_from_offsets(doc,
                                                   [(ent[0], ent[1], ent[2]) for ent in resume[1]["entities"]])

    
    doc_tokens = [tok.text for tok in doc]
    bilou_df = pd.DataFrame()
    bilou_df["Tokens"] =doc_tokens
    bilou_df["Tokens"] = bilou_df["Tokens"].str.replace("\\s+","") 
    bilou_df["Predicted"] = bilou_ents_predicted
    bilou_df["True"] = bilou_ents_true
    return bilou_df

In [51]:
data = []
for label in chosen_entity_labels:
    ## variables to store results for all resumes for one entity type
    true_positives = 0
    false_positives = 0
    false_negatives = 0
    for tres in test:
        
        ## use make_bilou_df on each resume in our test set, and calculate for each entity true and false positives,
        ## and false negatives. 
        tres_df = make_bilou_df(custom_nlp,tres)
        ## calculate true false positives and false negatives for each resume
        tp = len(tres_df.loc[tres_df["True"].str.contains(label)].loc[tres_df["Predicted"] == tres_df["True"]])
        fp = len(tres_df.loc[tres_df["True"] == "O"].loc[tres_df["Predicted"].str.contains(label)])
        fn = len(tres_df.loc[tres_df["True"].str.contains(label)].loc[tres_df["Predicted"] == "O"])

        ## aggregate result for each resume to totals
        true_positives += tp
        false_positives += fp
        false_negatives += fn
    
    print("For label '{}' tp: {} fp: {} fn: {}".format(label,true_positives,false_positives,false_negatives))
    
    ## TODO Use the formulas you learned to calculate metrics and print them out        
    precision = true_positives/(true_positives+false_positives)
    recall = true_positives/(true_positives+false_negatives)
    f1 = 2 * (precision*recall)/(precision+recall)
    #print("Precision: ",precision)
    #print("Recall: ",recall)
    #print("F1: ",f1)
    row = [precision,recall,f1]
    data.append(row)

## make pandas dataframe with metrics data. Use the chosen entity labels as an index, and the metric names as columns. 
metric_df = pd.DataFrame(data, columns = ['precision', 'recall', "f1"], index = chosen_entity_labels) 
display(metric_df)

For label 'Name' tp: 456 fp: 101 fn: 28
For label 'Skills' tp: 108 fp: 41 fn: 1905
For label 'Designation' tp: 594 fp: 130 fn: 87
For label 'Companies worked at' tp: 476 fp: 13 fn: 227
For label 'College Name' tp: 258 fp: 99 fn: 20


precision    recall        f1
Name                  0.818671  0.942149  0.876081
Skills                0.724832  0.053651  0.099907
Designation           0.820442  0.872247  0.845552
Companies worked at   0.973415  0.677098  0.798658
College Name          0.722689  0.928058  0.812598

In [52]:
from pdfminer.pdfinterp import PDFResourceManager, PDFPageInterpreter
from pdfminer.pdfpage import PDFPage
from pdfminer.converter import XMLConverter, HTMLConverter, TextConverter
from pdfminer.layout import LAParams
from io import StringIO
import docx2txt

In [53]:
def extract_text_from_pdf(data):

    fp = open(data, 'rb')
    rsrcmgr = PDFResourceManager()
    retstr = StringIO()
    codec = 'utf-8'
    laparams = LAParams()
    device = TextConverter(rsrcmgr, retstr, laparams=laparams)
    # removed from the line above: , codec=codec
    # Create a PDF interpreter object.
    interpreter = PDFPageInterpreter(rsrcmgr, device)
    # Process each page contained in the document.

    for page in PDFPage.get_pages(fp):
        interpreter.process_page(page)
        data =  retstr.getvalue()

    return data

def extract_text_from_doc(data):

    temp = docx2txt.process(data)
    text = [line.replace('\t', ' ') for line in temp.split('\n') if line]
    return ' '.join(text)

In [55]:
new_resume = extract_text_from_pdf('/Users/shishen/Insight_Data_Science/Resume_Standardization/data/SF_Resume.pdf')

In [56]:
doc = custom_ner(new_resume)
displacy.render(doc, style="ent",jupyter=True)

In [57]:
def convert_dataturks_to_spacy(dataturks_JSON_FilePath):
    try:
        training_data = []
        lines=[]
        with open(dataturks_JSON_FilePath, 'r') as f:
            lines = f.readlines()

        for line in lines:
            data = json.loads(line)
            text = data['content']
            entities = []
            for annotation in data['annotation']:
                #only a single point in text annotation.
                point = annotation['points'][0]
                labels = annotation['label']
                # handle both list of labels or a single label.
                if not isinstance(labels, list):
                    labels = [labels]

                for label in labels:
                    #dataturks indices are both inclusive [start, end] but spacy is not [start, end)
                    entities.append((point['start'], point['end'] + 1 ,label))


            training_data.append((text, {"entities" : entities}))

        return training_data
    except Exception as e:
        logging.exception("Unable to process " + dataturks_JSON_FilePath + "\n" + "error = " + str(e))
        return None

In [63]:
ds_resume = convert_dataturks_to_spacy('/Users/shishen/Insight_Data_Science/Resume_Standardization/data/DS_Resume.json')

In [65]:
custom_ds_ner,_ = train_spacy_ner(ds_resume, model='custom_ner', n_iter = 20, debug=False)

Loaded model 'custom_ner'
Losses {'ner': 1188.0784378948156}
Losses {'ner': 1462.6670136116445}
Losses {'ner': 926.287785837194}
Losses {'ner': 1057.111437372514}
Losses {'ner': 835.0239719119854}
Losses {'ner': 731.6299844051246}
Losses {'ner': 953.0825657329988}
Losses {'ner': 700.2690794290975}
Losses {'ner': 810.6002507903031}
Losses {'ner': 1203.8479962651618}
Losses {'ner': 1059.7803180832416}
Losses {'ner': 695.8996868082322}
Losses {'ner': 610.0352378988173}
Losses {'ner': 630.7811251452658}
Losses {'ner': 610.5897034705849}
Losses {'ner': 588.0466893067205}
Losses {'ner': 525.3300578794442}
Losses {'ner': 527.1195897386642}
Losses {'ner': 547.7873314695062}
Losses {'ner': 467.0676239034801}


In [66]:
save_spacy_model(custom_ds_ner, '/Users/shishen/Insight_Data_Science/Resume_Standardization/custom_ds_ner/')

Saved model to /Users/shishen/Insight_Data_Science/Resume_Standardization/custom_ds_ner


In [67]:
doc = custom_ds_ner(a)
displacy.render(doc, style="ent",jupyter=True)

In [68]:
doc.ents

(SHIWAN FENG,
 Data Analyst/Data Scientist,
 Miner 14.1,
 SQL,
 Hive,
 Spark,
 SparkSQL,
 Data Analysis,
 R,
 SAS,
 SPSS,
 Microsoft,
 MySQL,
 Oracle,
 SQL,
 Python,
 Tableau,
 Shiny,
 Data Scientist,
 University of Connecticut,
 Student Consultant,
 Data Scientist,
 Data Analyst,
 University of Connecticut,
 Shanghai University of Finance and Economics)